# Part 1: S&P 500 Stock Price Forecast
> **Motivation:**  Beginning in March 2020 during the COVID pandemic, the stock market soared unexpectedly. I want to know if Machine learning could have predicted this trend 
using LSTM ... fiill

In [50]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import plotly.graph_objects as go
import plotly.express as px
import datetime
import yfinance as yf
from scipy import stats

from sklearn.preprocessing import MinMaxScaler
from sklearn.linear_model import LinearRegression
import keras.backend as K
from keras.models import Sequential
from keras.layers import LSTM
from keras.layers import Dropout
from keras.layers import Dense
from keras.callbacks import EarlyStopping

## I) EDA

In [51]:
def candlestick(df, title, begin_year='1975'):
    # Plot candlestick chart
    temp = df[df.index > begin_year]
    fig = go.Figure(data=[go.Candlestick(x=temp.reset_index()['Date'],
                open=temp['Open'],
                high=temp['High'],
                low=temp['Low'],
                close=temp['Adj Close'])])
    
    fig.update_layout(title=title,
                      yaxis_title="USD")

    fig.show()

### Analyze the Stock Market
The S&P 500 Index is largely considered an essential benchmark of the stock market. I will analyze it to gain insight about the market

In [52]:
SP500 = yf.download('^GSPC')

[*********************100%***********************]  1 of 1 completed


In [53]:
# Generic plot of S&P 500 stock price 
candlestick(SP500,'S&P 500: Market Summary')

In [54]:
def annual_percent_change(df):
    # Calculates percent annual return
    # Input: df[Date, Open, High, Low, Close, Adj Close]
    # Output: df[Year, Open, High, Low, Close, % Change]] 
    
    years = np.unique(np.array(SP500.index.year))[0:-1]
    percent_change = []
    year_open, year_close = [], [] 
    year_low, year_high = [], []

    for i in years:
        temp = df[(df.index >= str(i)) & (df.index < str(i+1))]['Adj Close']
        percent_change.append(round((temp[-1] / temp[0] - 1) * 100, 2))
        year_open.append(temp[0])
        year_close.append(temp[-1])
        year_low.append(min(temp))
        year_high.append(max(temp))
    
    result = pd.DataFrame({'Date':years, 
                         'Open': year_open,
                         'Close': year_close,
                         'Low': year_low,
                         'High': year_high,
                         '% Change': percent_change}).set_index('Date')
    return result 

SP500_YoY = annual_percent_change(SP500)

In [55]:
average_annual_return = np.mean(SP500_YoY[SP500_YoY.index >= 1950]['% Change'])

SP500_2019 = SP500_YoY[SP500_YoY.index == 2019]['% Change']
SP500_2020 = SP500_YoY[SP500_YoY.index == 2020]['% Change']
SP500_2021 = SP500_YoY[SP500_YoY.index == 2021]['% Change']

SP500_2019, SP500_2020, SP500_2021, average_annual_return

(Date
 2019    28.71
 Name: % Change, dtype: float64,
 Date
 2020    15.29
 Name: % Change, dtype: float64,
 Date
 2021    28.79
 Name: % Change, dtype: float64,
 8.894246575342464)

> The S&P500 index has delivered an average annual growth rate of 8.7% since 1950. However, this rule of thumb did not apply during the pandemic.
> * In 2019, S&P 500 grew  **29%**
> * In 2020, S&P 500 grew **15%**
> * In 2021, S&P 500 grew **29%** 

In [56]:
# Plot % Annual Growth
temp = SP500_YoY[SP500_YoY.index > 1950].reset_index() # Only include recent data, (1950 and beyond)
fig = px.bar(temp, x="Date", y="% Change", title='S&P 500: Annual Growth')
fig.update_layout(xaxis_title='Year', yaxis_title='Percent Annual Growth (%)')

In [57]:
# Calculate percentile 
stats.percentileofscore(SP500_YoY['% Change'], SP500_2019), stats.percentileofscore(SP500_YoY['% Change'], SP500_2020), stats.percentileofscore(SP500_YoY['% Change'], SP500_2021)

(array([90.625]), array([64.58333333]), array([91.66666667]))

>The plot above shows the percent annual growth in price between 1950 and 2022. We occasionally see long positive streches, often followed by a big negative year. The 2019-2022 market is certainly bullish, with a growth rate in the **90th, 60th, and 90th percentile** which is reminiscent of the **dot-com bubble in the late 90s.**


## II) Modeling and Prediction: one day in the future
* **Objective**: Predict stock prices one day in advance. 

* Because future stock prices are very reliant on past prices, I will use the LSTM model which stores past information better than simple RNNs

### Preprocessing

In [93]:
def split(df, split_ratio):
    # Takes in a df and splits it into train and test df
    
    numrows_train = round(split_ratio * df.shape[0])
    train_df = df[0:numrows_train]
    test_df = df[numrows_train:]
    return train_df, test_df

In [94]:
df = SP500
split_ratio = 0.7

train_df, test_df = split(df, split_ratio)

In [95]:
def offset(array, n_features, lookahead):
    # array: an array of normalized training or test data
    # n_features: use past n days of data as the feature to predict price
    # lookahead: how many days in the future you want to predict
        # Output: x_train and y_train
    x, y = [], []
    
    for i in range(n_features, len(array)-lookahead+1):
        x.append(array[i-n_features:i])
        y.append(array[i+lookahead-1, 0])

    return np.array(x), np.array(y)

In [96]:
scaler = MinMaxScaler(feature_range = (0,1))
n_features = 60 # Use the last 60 days as a feature
lookahead = 1 # Predict stock prices 1 day in advance. So tomorrow's prices

# Normalize training and test data
train_scaled = scaler.fit_transform(train_df['Adj Close'].values.reshape(-1,1))
test_scaled = scaler.fit_transform(test_df['Adj Close'].values.reshape(-1,1))

x_train, y_train = offset(train_scaled, n_features, lookahead)
x_test, y_test = offset(test_scaled, n_features, lookahead)

### Build model
Future stock prices are very reliant on past prices, so I will use the LSTM model that can <...>

In [97]:
def build_model():
    K.clear_session()
    model = Sequential()

    model.add(LSTM(units = 50, return_sequences = True, input_shape = (x_train.shape[1],1)))
    model.add(Dropout(0.2))

    model.add(LSTM(units = 50, return_sequences = True))
    model.add(Dropout(0.2))

    model.add(LSTM(units = 50))
    model.add(Dropout(0.2))

    model.add(Dense(units=1))
    
    return model

In [98]:
model = build_model()
model.compile(loss='mean_squared_error', optimizer='adam')
early_stop = EarlyStopping(monitor='loss', patience=10, verbose=1)

### Train model

In [99]:
model = build_model()
model.compile(loss='mean_squared_error', optimizer='adam')

model.fit(x_train, y_train, epochs=6, 
          batch_size = 32)

Epoch 1/6
521/521 [==============================] - 14s 22ms/step - loss: 0.0016
Epoch 2/6
521/521 [==============================] - 12s 23ms/step - loss: 6.7709e-04
Epoch 3/6
521/521 [==============================] - 12s 23ms/step - loss: 6.3368e-04
Epoch 4/6
521/521 [==============================] - 12s 23ms/step - loss: 6.2067e-04
Epoch 5/6
521/521 [==============================] - 12s 23ms/step - loss: 5.0948e-04
Epoch 6/6
521/521 [==============================] - 12s 23ms/step - loss: 5.6159e-04


In [100]:
## Runtime Optimization, the model did not improve much past 6 epochs
# epoch, loss = [], []

# for i in range(3, 10): # Optimal num epoch
#     model = build_model()
#     model.compile(loss='mean_squared_error', optimizer='adam')
#     early_stop = EarlyStopping(monitor='loss', patience=10, verbose=1)

#     model.fit(x_train, y_train, epochs=i, 
#   batch_size = 32)
    
#     epoch.append(i)
#     loss.append(model.evaluate(x_test, y_test))

### Predict and analyze results

In [118]:
test_pred = model.predict(x_test)
test_pred = scaler.inverse_transform(test_pred)

222/222 [==============================] - 2s 8ms/step


In [123]:
##
test_pred = model.predict(x_test)

222/222 [==============================] - 2s 8ms/step


In [127]:
##
# temp = pd.DataFrame({'true': y_test, 'pred': test_pred.flatten()})
# px.line(temp, y = ['true', 'pred'])
test_pred

array([[0.00503126],
       [0.00501484],
       [0.00497116],
       ...,
       [0.8014183 ],
       [0.8032519 ],
       [0.8052104 ]], dtype=float32)

In [103]:
summary_df = test_df[n_features:].reset_index()
summary_df['Forecasted'] = test_pred

In [104]:
fig = px.line(summary_df, x="Date", y=["Forecasted", 'Adj Close'], title='S&P 500: Summary and Forecast')
fig.show()

> Although there are slight deviations on a day-to-day basis, the model accurately captures the overall market trends.

In [69]:
# RMSE
summary_df['Squared Loss'] = (summary_df['Forecasted'] - summary_df['Adj Close'])**2
RMSE = np.sqrt(summary_df['Squared Loss'].mean())
RMSE

55.3687916793023

In [70]:
# Plot Square Error
px.scatter(summary_df, x='Date', y='Squared Loss', title = 'S&P500: Squared Loss')

> The above scatterplot plots the **squared loss** of our model. Notice that the model has high loss everytime there is a economic turmoil (like in the late 90s and 2009s). However, the model unequivocally had the **highest loss during lockdown**. It appears like the model **failed to predict the volatility of the market at the onset of the pandemic.**

In [71]:
summary_df.sort_values('Squared Loss', ascending=False)[0:10]

Date         Open         High          Low        Close  \
3994 2020-03-16  2508.590088  2562.979980  2380.939941  2386.129883   
3992 2020-03-12  2630.860107  2660.949951  2478.860107  2480.639893   
3996 2020-03-18  2436.500000  2453.570068  2280.520020  2398.100098   
3999 2020-03-23  2290.709961  2300.729980  2191.860107  2237.399902   
3998 2020-03-20  2431.939941  2453.010010  2295.560059  2304.919922   
3989 2020-03-09  2863.889893  2863.889893  2734.429932  2746.560059   
3997 2020-03-19  2393.479980  2466.969971  2319.780029  2409.389893   
3995 2020-03-17  2425.659912  2553.929932  2367.040039  2529.189941   
3982 2020-02-27  3062.540039  3097.070068  2977.389893  2978.760010   
3983 2020-02-28  2916.899902  2959.719971  2855.840088  2954.219971   

        Adj Close      Volume   Forecasted   Squared Loss  
3994  2386.129883  7805450000  2969.899170  340786.580572  
3992  2480.639893  8850810000  3061.185791  337033.540193  
3996  2398.100098  8799300000  2859.872314  213233.580206  
3999  2237.399902  7411380000  2686.520752  201709.537554  
3998  2304.919922  9053950000  2744.394043  193137.503111  
3989  2746.560059  8441290000  3156.107666  167729.242745  
3997  2409.389893  7956100000  2801.943115  154098.032618  
3995  2529.189941  8370250000  2915.833252  149493.049591  
3982  2978.760010  7064710000  3358.163330  143946.879464  
3983  2954.219971  8569570000  3333.445557  143812.045030

> This table tells us the **ten highest errors of all time occured between February and June of 2020.**

In [72]:
# Plot Error
summary_df['Residual'] = summary_df['Forecasted'] - summary_df['Adj Close']
fig = px.scatter(summary_df[summary_df['Date'] > '2005'], 
           x='Date', y='Residual', title = 'S&P500: Residual Scatterplot')
fig.add_hline(y=0)
fig.show()

**Other observations:**
> * From the residual scatterplot, we can see that the model greatly **overestimated the index value in early March 2020, then underestimated in April**

# Part 2) Tech Stocks
NASDAQ 100 Technology Sector (NDXT) is an index composed of tech companies like Alphabet, Apple, and Meta (Facebook). Growth in the tech sector was even more pronounced during the pandemic.

In [73]:
df = yf.download('^NDXT')

[*********************100%***********************]  1 of 1 completed


In [74]:
split_ratio = 0.75
train_df, test_df = split(df, split_ratio)
scaler = MinMaxScaler(feature_range = (0,1))

In [75]:
n_features = 30
lookahead = 1

# Normalize training and test data
train_scaled = scaler.fit_transform(train_df['Adj Close'].values.reshape(-1,1))
test_scaled = scaler.fit_transform(test_df['Adj Close'].values.reshape(-1,1))

x_train, y_train = offset(train_scaled, n_features, lookahead)
x_test, y_test = offset(test_scaled, n_features, lookahead)

In [76]:
model = build_model()
model.compile(loss='mean_squared_error', optimizer='adam')

model.fit(x_train, y_train, epochs=6, 
          batch_size = 32)

Epoch 1/6
99/99 [==============================] - 4s 12ms/step - loss: 0.0076
Epoch 2/6
99/99 [==============================] - 1s 12ms/step - loss: 0.0020
Epoch 3/6
99/99 [==============================] - 1s 12ms/step - loss: 0.0017
Epoch 4/6
99/99 [==============================] - 1s 12ms/step - loss: 0.0017
Epoch 5/6
99/99 [==============================] - 1s 12ms/step - loss: 0.0016
Epoch 6/6
99/99 [==============================] - 1s 12ms/step - loss: 0.0014


In [77]:
test_pred = model.predict(x_test)
test_pred = scaler.inverse_transform(test_pred)

33/33 [==============================] - 1s 4ms/step


In [78]:
summary_df = test_df[n_features:].reset_index()
summary_df['Forecasted'] = test_pred

In [79]:
fig = px.line(summary_df, x="Date", y=["Forecasted", 'Adj Close'], title='S&P 500: Summary and Forecast')
fig.show()

In [80]:
# RMSE
summary_df['Squared Loss'] = (summary_df['Forecasted'] - summary_df['Adj Close'])**2
RMSE = np.sqrt(summary_df['Squared Loss'].mean())
RMSE

319.13149714456387

In [81]:
# Plot Error
summary_df['Residual'] = summary_df['Forecasted'] - summary_df['Adj Close']
fig = px.scatter(summary_df[summary_df['Date'] > '2005'], 
           x='Date', y='Residual', title = 'S&P500: Residual Scatterplot')
fig.add_hline(y=0)
fig.show()

# Part 3) Apple (AAPL) 

The RMSE is much higher than before, and the residual plot shows wild inconsistencies. 

In [82]:
df = yf.download('AAPL')

[*********************100%***********************]  1 of 1 completed


In [83]:
split_ratio = 0.65
train_df, test_df = split(df, split_ratio)
scaler = MinMaxScaler(feature_range = (0,1))

In [84]:
n_features = 30
lookahead = 1

# Normalize training and test data
train_scaled = scaler.fit_transform(train_df['Adj Close'].values.reshape(-1,1))
test_scaled = scaler.fit_transform(test_df['Adj Close'].values.reshape(-1,1))

x_train, y_train = offset(train_scaled, n_features, lookahead)
x_test, y_test = offset(test_scaled, n_features, lookahead)

In [85]:
model = build_model()
model.compile(loss='mean_squared_error', optimizer='adam')

model.fit(x_train, y_train, epochs=6, 
          batch_size = 32)

Epoch 1/6
215/215 [==============================] - 6s 13ms/step - loss: 0.0016
Epoch 2/6
215/215 [==============================] - 3s 13ms/step - loss: 6.4466e-04
Epoch 3/6
215/215 [==============================] - 3s 13ms/step - loss: 5.3974e-04
Epoch 4/6
215/215 [==============================] - 3s 13ms/step - loss: 5.0693e-04
Epoch 5/6
215/215 [==============================] - 3s 13ms/step - loss: 4.5172e-04
Epoch 6/6
215/215 [==============================] - 3s 13ms/step - loss: 5.5323e-04


In [86]:
test_pred = model.predict(x_test)
test_pred = scaler.inverse_transform(test_pred)

116/116 [==============================] - 1s 5ms/step


In [87]:
summary_df = test_df[n_features:].reset_index()
summary_df['Forecasted'] = test_pred

In [88]:
fig = px.line(summary_df, x="Date", y=["Forecasted", 'Adj Close'], title='')
fig.show()

In [89]:
# RMSE
summary_df['Squared Loss'] = (summary_df['Forecasted'] - summary_df['Adj Close'])**2
RMSE = np.sqrt(summary_df['Squared Loss'].mean())
RMSE

3.2848843176244467

In [90]:
# Plot Square Error
px.scatter(summary_df, x='Date', y='Squared Loss', title = 'S&P500: Squared Loss')